## Investigation Module 3: Elliptic Curves and Lenstra's Factoring Algorithm

### Introduction
In this investigation module, you will implement an algorithm for quickly finding factors of larger integers. This algorithm is known as the *Lenstra's elliptic-curve factorization*, and makes use of group properties of elliptic curves. We will first review these properties, and implement methods for taking sums and scalar products in these groups. Afterwards, we will give a description of Lenstra's algorithm, and you will be asked to write a Sage implementation.

### Elliptic Curves

Recall that an **elliptic curve** $E$ over a field $F$ is defined to be the set of all points $(x,y)$ satisfying $y^2 = x^3 + ax^2 + bx + c$ for some $a,b,c \in F$. One of the neat things about (non-singular) elliptic curves is that their points form a group when we operate on them the right way. This group interpretation relies on the fact that (up to some stretching and pulling about what we mean by words like "exactly", "intersect", and "points") a line $L$ intersecting $E$ through points $P$ and $Q$ will intersect $E$ at a third point. These lines usually fall into one of four categories: a vertical tangent line, a vertical non-tangent line, a non-vertical tangent line, or a non-vertical, non-tangent line (the "typical" case). It may at first seem untenable that a vertical tangent to the curve intersects the curve at three points, and that's where the stretching and pulling comes in. To begin with, if a line $L$ is tangent to a curve $E$ at a point $P$, then we count that point $P$ twice instead of just once (and in very rare cases, three times), similar to how we count multiple zeros of polynomials that "touch" the x-axis, but do not cross it. As for the third point, we introduce a "point at infinity", which we define to be the intersection of all vertical lines in the plane, and make it part of our elliptic curve (other points at infinity can be made for other classes of parallel lines, but for our purposes just this one will do). Using these conventions, we can confidently say any line $L$ given by two (not necessarily distinct) points $P$ and $Q$ of intersection to $E$ has a third point of intersection $R$.

The preceding discussion is rather informal. In counting a tangent point as two points we're really counting two points as two points, except that the points are getting infintesimally close to each other via a limit, and although you have discussed it in detail in the course, a formal treatment of points at infinity is beyond the scope of this module. Still, these conventions enable us to impose a group structure on the points of the curve under the following axioms:

1. The point at infinity, $O$, is the identity element.
2. If a line intersects the elliptic curve in three points $P$, $Q$, and $R$, then $P + Q + R = O$.
3. The inverse of a point $P = (x,y)$ is $-P = (x,-y)$.

Of particular interest is axiom 2, which tells us how to apply the operation to elements in the group: Given two points $P$ and $Q$, we have that $P + Q = -R$, where $R$ is the third point of intersection on the curve. Considering first the "typical" line configuration (as it is the most interesting), we first want to construct the line intersecting $P$ and $Q$ on the curve, and then see where this line intersects the curve a third time. Before we do this, we note that the right-hand side of the equation defining an elliptic curve need not have an $x^2$ term, as we are not concerned about the horizontal location of the curve in the plane (see Daily Update 11.1.2), and we will fix the notation $y^2 = x^3 + ax + b$.

We have that
$$
y = \frac{y_Q - y_P}{x_Q - x_P}(x-x_P) + y_P = Mx + B
$$
is the line passing through $P$ and $Q$. Our search for the third point $R = (x_R,y_R)$ involves finding the third solution to the cubic equation
$$
(Mx + B)^2 = x^3 + ax + b
$$
We omit the details, and instead just give the coordinates for $R$
$$
x_R = M^2 - x_P - x_Q
$$
$$
y_R = M(x_R - x_P) + y_P
$$
Finally, since $P + Q = -R$, we have $P + Q = (x_R,-y_R)$.

In our computation of $-R$ for the "typical" case, our formulas for the coordinates of $R$ actually hold for the general case, as long as we use  our conventions regarding points on lines, and for the slope $M$. If $P \neq Q$ and the line between them is non-vertical, then $M$ is simply the slope between $P$ and $Q$ (i.e., $(y_Q - y_P) / (x_Q - x_P)$). If the line between them is vertical, then the slope will be $\infty$ and the third point on intersection is taken to be $O$, which makes sense since the two points on the vertical line are inverses of each other ($P + Q + O = O \iff P = -Q$). Specifically, in the vertical tangent case we have that $P + P + O = O \Rightarrow 2P = O$. Finally, if $P = Q$ and the tangent line to $P$ is non-vertical, then $M$ is the slope of the tangent line to the curve at $P$, and we have $P + P + R = O \Rightarrow 2P = -R$ for $R$ computed as above.  (Note that in rare cases, $R=P$, so the $3P=P+P+P=O$, and $P$ is considered to count "three times".) Thus the coordinate for $R$ are given by
$$
x_R = \left(\frac{dy}{dx}(P)\right) - 2x_P
$$
$$
y_R = \left(\frac{dy}{dx}(P)\right)(x_R - x_P) + y_P
$$
and so $2P = (x_R,-y_R)$. This last formula is often called the *doubling formula*, as it tells us how to "double" a point on the curve. Note that, implicitly differentiating our elliptic equation $y^2 = x^3 + ax + b$ , we have $\frac{dy}{dx} = \frac{3x^2 + a}{2y}$, which is taken to be infinity if the numerator is nonzero and the denominator is zero.

#### Curves Modulo a Number

**Elliptic curves modulo $n$** are defined to be sets of solutions to congruences of the form $y^2 \equiv x^3 + ax + b\mod n$, where $a,b,x$ and $y$ are all over $\mathbb{Z}/n\mathbb{Z}$. Note that, if $n$ is not prime, $\mathbb{Z}/n\mathbb{Z}$ is not a field!  In this case, our axioms need not make points $(x,y)$ satisying our elliptic curve equation into a group, since given two points, their sum may not well-defined. This is because, in our addition and doubling formulas, we must compute a slope $M$, understood modulo $n$, requiring us to find the inverse of the denominator modulo $n$.  For instance, suppose that we are working modulo $6$. If we calculate a slope between two points as $\frac{2}{5}$, we can consider this as $2$ multpilied by the multiplicative inverse of $5$ modulo $6$, which is again $5$, so $M \equiv 2 \cdot 5 \equiv 4 \bmod 6$.  On the other hand, if we calculate the slope $\frac{1}{2}$, we cannot consider this as the multiplicative inverse of $2$ modulo $6$, since it doesn't exist!
Hence we have no way of adding the corresponding points. 

Amazingly, as we will soon see, though, this obstotacle toward adding two points modulo $n$ is exactly what we want to happen when are seeking to apply elliptic curves to factor integers. For the time being, though, let's implement some group laws!

### Exercise 1: Elliptic Point Addition Modulo $n$

In this exercise, you will write a function to compute $P + Q$ for two points $P, Q$ on an elliptic curve modulo $n$. The theory developed in the first section of general elliptic curves will work with elliptic curves mod $n$, so long as the computations made along the way are possible when interpreted modulo $n$. 

One way to start writing this function is to first determine just what kind of points $P$ and $Q$ are. If $P$ is the point at infinity $O$, then the sum will just result in $Q$ (and vice versa). If neither $P$ nor $Q$ is the identity, then there should be a line passing through them, in which case we need to check whether if it is one of the four cases described above (vertical tangent, vertical non-tangent, non-vertical tangent, or non-vertical, non-tangent), and compute the point $-R$ using the appropriate formula (modulo $n$, of course!). As noted in the previous section, it is possible that some points on the curve just can't be added due to a non-unit denominator in the slope. In this case, the function should return something signifying that the addition failed. For this purpose, we can use the Sage built-in name `None`. If you find that the addition fails, just `return (None, g)` (where $g > 1$ is the common factor between the slope's denominator and $n$. Our reasoning for returning `g` along with `None` will become apparent later). It's also possible that the sum results in the identity point at infinity. You can use anything you want to identify this point so long as it is not an actual point on the curve. We recommend just using the constant `0` for this purpose.

As an example sketch implementation, your function might look something like this; think about why proceeding in this order will work!

Let $P$ and $Q$ lie on $y^2 \equiv x^3 + ax + b \mod n$

1. If $P$ or $Q$ is the identity $O$, then return the other
2. Otherwise, $P = (x_1,y_1)$, $Q = (x_2,y_2)$
3. If $P = Q$, then the intersecting line is tangent.

    3a. If $2y_1 \mod n = 0$, then the tangent line is vertical, return $O$ (since $2y_1$ modulo $n$ is the denominator of the slope of the tangent line).
    
    3b. Otherwise, the tangent line is non-vertical; the slope is $((3x_1^2 + a \mod n) / (2y_1 \mod n))$
    
4. Otherwise, the points are not coincident and the intersecting line is not tangent.

    4a. If $(x_2 - x_1) \equiv 0 \mod n$, then the line is non-tangent and vertical; return $0$ (notice that $x_2 - x_1$ is the denominator of the slope of the intersecting line).
    
    4b. Otherwise, the line is non-tangent and non-vertical; the slope is $(y_2 - y_1) / (x_2 - x_1)$
    
5. Set $den :=$ the denominator of the slope; set $num :=$ the numerator of the slope (considered modulo $n$).

    5a. If $\gcd(den, n) \ne 1$, then the denominator is not a unit modulo $n$, and so we cannot invert the denominator. Return None.
    
    5b. Otherwise, set $m :=$ the multiplicative inverse of $den$ modulo $n$; set $M := (m * num)$ modulo $n$ to invert the denominator of the slope.
    
6. Finally, as long as None was not returned in Step 5, we have that $P + Q = (M^2 - x_P - x_Q, M(x_P - x_R) - y_P)$, taking the coordinates modulo $n$; return this point.

Steps 3 and 4 are pretty much just checking to see what kind of line is intersecting $P$ and $Q$, and giving appropriate values to the slope. Step 5 is checking to see if the denominator of the slope is invertible, and multiplying the numerator by the inverse. Step 6 is where the actual computation of the point happens, after we have checked to make sure everything is OK. Here, you will need a function to compute inverses modulo $n$. You are free to use your `eea` function from the previous module if you wish. We have also provided implementations of the tools you will need to get this done, if you would rather use those. Those functions are `xgcd` and `modinv`, discussed below.

You might be wondering how to write your function that can make all these branching decisions. So far, the only Sage control-flow structure we have gone over in our Programming Investigation Modules are looping structures. However, there is a control flow structure which is even more basic and essential to programs than loops.

#### Sage Interlude: `if`, `else`, `elif`, and Tuples

Remember that control flow is all about enabling the program to do different things under different circumstances. This behavior is best demonstrated in a structure called an `if` block. `if` blocks have the following form.

```
if (<expression>):
    <code>
```

Read: "If `<expression>` is true, then `<code>` will be executed." Conversely, if `<expression>` turns out false, then `<code>` will be skipped. As an example, consider Step 4a in the algorithm above. We can implement this step using an `if` block as follows:

```
if ((x_2 - x_1) % n == 0):
    return 0
```

We can also tell Sage what to do if the expresson turns out false using `else`.

```
if (<expression>):
    <code_true>
else:
    <code_false>
```

This way, Sage can handle the "otherwise" case. Note that when using this form, one of `<code_true>` or `<code_false>` is *guaranteed* to execute. Specifically, if `<expression>` is false, then `<code_false>` will run. Otherwise `<code_true>` will run.

Finally, it is sometimes the case that we want to check multiple conditions before falling back on a catch-all `else` case. One way we could do this is as follows

```
if (<expression1>):
    <code_true1>
else:
    if (<expression2>):
        <code_true2>
    else:
        if (<expression3>):
            <code_true3>
        else:
            .
                .
                    .
                        if (expressionWhoKnows):
                            <code_trueWhoKnows>
                        else:
                            <code_CatchAll>
```

As you can see, code readability begins to become an issue if we keep nesting `if...else` blocks inside of each other. This is why most programming languages, including Sage, offer an "Else-If" block.

```
if (<expression1>):
    <code_true1>
elif (<expression2>):
    <code_true2>
elif (<expression3>):
    <code_true3>
.
.
.
elif (<expressionWhoKnows>):
    <code_WhoKnows>
else:
    <code_CatchAll>
```

Using this form, we can have a chain of different bodies of code to execute based on differing conditions. The way Sage decides which code body to run is it tests each of the `expression`s in order, and runs the first code block who's expression evaluates to true.

As a last bit of Sagely advice (ha ha), we introduce the **tuple** data structure. Remember lists? Well, tuples are pretty much just those, only their contents and size are unchangable (*immutable*, in jargon-speak). Tuples in Sage have the form `(a1,a2,...,an)`. The only reason we introduce them here is that they are particularly suitable for expressing coordinates. For example, if we're trying to return some point on a curve, and we have coordinates `x_R` and `y_R` computed, we can wrap these coordinates up into a tuple and return that (e.g., `return (x_R, y_R)`). Tuples can also be *unpacked*. Suppose `P` is some variable that we know stores a coordinate point in a tuple, and we want to store the x- and y-coordinates of that point so that we can work with them later. One way to do that would be by indexing, i.e., we could say `x_1 = P[0]` and `y_1 = P[1]` (the same way we access list elements). Another way, though, is through unpacking. If we know that `P` is a tuple of length 2, then we can just say `x_1, y_1 = P`, and Sage will pull out the components of that tuple and put them into the variables that we want automatically. But we can do this with lists too! So what's the big deal with tuples? Well, aside from the semantic distinction of being immutable, there's really not much of a difference, though it could be argued that we really don't want to be able to *change* the points that we are using for our computations, and so we can loosly justify their use on those grounds. Basically, use them, or don't, but know that they're there!

### Provided Helper Functions
We provide an efficient implementation of the extended euclidean algorithm `xgcd` as well as a function `modinv` to compute the inverse of an integer $a$ modulo $b$. You are free to use them. Note that both of these functions return multiple things at the same time. In particular, `modinv` returns both the modular inverse of a number modulo $b$, and the gcd of $a$ and $b$. You can get access to both of these values by unpacking what is returned, like so:
```
a = 2
ai, g = modinv(a, 5)
```
Now `ai` should evaluate to 3, and `g` should evaluate to 1. You can use `g` as a check to see if a modular inverse of $a$ exists modulo $b$, since if $g = \gcd(a,b) \ne 1$, no modular inverse exists.

In [8]:
def xgcd(a, b):
    """
    return (g, x, y) such that a*x + b*y = g = gcd(a, b)
    credit https://en.wikibooks.org/wiki/Algorithm_Implementation/Mathematics/Extended_Euclidean_algorithm
    """
    x0, x1, y0, y1 = 0, 1, 1, 0
    while a != 0:
        (q, a), b = divmod(b, a), a
        y0, y1 = y1, y0 - q * y1
        x0, x1 = x1, x0 - q * x1
    return b, x0, y0

def modinv(a, b):
    """
    return x such that (x * a) % b == 1
    credit https://en.wikibooks.org/wiki/Algorithm_Implementation/Mathematics/Extended_Euclidean_algorithm
    """
    g, x, _ = xgcd(a, b)
    return x % b, g

In [4]:
#EXERCISE 1: Addition of two points on an elliptic curve E
#INPUT: Two points P and Q; coefficient a and constant b in y^2 = x^3 + ax + b (needed for tangent slope computation); modulus of congruence n
def elliptic_add(P, Q, a, b, n):
    """
    INPUT
     - Points 'P' = (x1, y1) and 'Q' = (x2, y2)
     - Coefficients 'a' and 'b' defining the elliptic curve y^2 = x^3 + ax + b
     - Modulus of congruence 'n'
    OUTPUT
     - Point R = P + Q
    """
    #First, check to see if either point is the identity; return the other if so
    if (P == 0):
        return Q
    elif (Q == 0):
        return P

    #Neither point is the identity; get the coordinate pair of each
    x1, y1 = P
    x2, y2 = Q

    #We need to make sure these points are actually solutions to the given elliptic curve;
    #we implement this for you. The function will throw an error if this does not hold
    assert((y1**2 - x1**3 - a*x1 - b) % n == 0),"P is not a point on the curve"
    assert((y2**2 - x2**3 - a*x2 - b) % n == 0),"Q is not a point on the curve"

    return # P + Q

### Exercise 2: Higher Multiples of Points

In additive groups, we can roughly define a form of multiplication (or exponentation) by an integer as repeated addition (multiplication, respectively). Thus, given a point $P$ on an elliptic curve, we can translate
$$
kP := \underbrace{P + P + \cdots + P}_{\textrm{\scriptsize$k$ times}}
$$
to define what it means to take a *multiple* of a point in this group, as we have already done for $2P = P+P$. Here you will write a function which implements this $k$-times repeated addition. Though beware: since we are adding points over a curve modulo $n$, $kP$ may not exist for some arbitrary $k$ for the same reason that it is sometimes impossible to add two of these points. Unless you have taken precautions in your addition function, you are going to want to make sure your multiplciation function catches when this happens, which will be when the addition function *first* returns `(None,g)`. To see if a value in Sage is `None`, you can use the `is` comparison operator:
```
if (a is None):
    <a_is_None_stuff>
```

In [5]:
def elliptic_mul(d, P, a, n):
    """
    INPUT
     - Positive integer 'd' with which to multiply 'P'
     - Point 'P'
     - Coefficient 'a' which when taken with 'P' and 'n' uniquely determines the coefficient 'b' defining the elliptic curve y^2 = x^3 + ax + b
     - Modulus of congruence 'n'
    OUTPUT
     - Point d*P
    """
    #Fixing coefficient 'a' and point 'P', we compute constant term 'b' for the curve
    if (P != 0):
        b = (P[1]**2 - P[0]**3 - a*P[0]) % n

    return # d*P

### Lenstra's Factoring Algorithm

Now that we can find multiples of points on an elliptic modulo $n$, we can finally get at why we would want to do such a laborious task in the first place. We know that sometimes it is impossible to add two points on this curve because we cannot find an inverse modulo $n$ of the denominator of the slope of the line passing through them. But wait a minute, if we can't find an inverse modulo $n$ of the denominator, then the denominator and $n$ are not relatively prime, and in checking to see if they are, we computed their gcd, which therefore must be a factor of $n$ that is non-trivial! So in of this whole process of adding two elliptic points, sometimes we have factors of $n$ that just "fall out" when the addition fails!

Unfortunately, a failure to add points modulo $n$ can sometimes fail to produce a proper factor of $n$. Sometimes it is the case that the denominator is actually a multiple of $n$ itself, in which case the gcd would be $n$; not very helpful for factoring.  (Notice that this phenomenon has an analog in Pollard's $p-1$ factoring algorithm, and the $p+1$ factoring algorithm!) If this happens when we are performing repeated addition of a single point $P$ on the curve, then in fact, this implies that $P$ has the same order over the curve modulo $p$ for each prime factor $p$ of $n$.

To see why this is true, note that if the denominator is a multiple of $n$, then it is also a multiple of all the prime factors $p$ of $n$. So, say $kP = O$ over the curve modulo $n$ for some $k$. In the first place, this implies that $P,2P,3P,\cdots,(k-1)P$ are all repeated additions that do not fail over the curve modulo $n$. Now, considering the curve modulo a prime factor $p$ of $n$, if $iP = O$ for $1 \le i \le k-1$ modulo $p$, then the denominator of the slope of the line passing through $(i-1)P$ and $P$ is congruent to $0$ modulo $p$, which is to say, a multiple of $p$. But if this denominator is a multiple of $p$, then it shares a non-trivial factor with $n$, and so the addition over the curve modulo $n$ should also have failed, which, as we have already established, it doesn't. Thus, the order of $P$ over the curve modulo $p$ is larger than $k-1$ for all prime factors $p$ of $n$. Finally, since $kP = O$ over the curve modulo $n$, the denominator of the slope of the line passing through $(k-1)P$ and $P$ must be congruent to 0 modulo $n$, which makes it a multiple of $n$, and thus a multiple of $p$. Hence, $kP = O$ over the curve modulo $p$ as well, and so $P$ has order $k$ over the curve modulo $p$ for all prime factors $p$ of $n$.

Thankfully, the case that Lenstra's algorithm fails to produce a proper factor of $n$ is pretty unlikely to happen. Given an integer $n$, an elliptic curve $E$, and a point on the curve $P$, that $P$ will have the same order over that curve mod *all* of $n$'s prime factors, even if $n$ is the product of two distinct primes. (Think about what we know about the order of an elliptic curve modulo a prime, along with Lagrange's theorem!) Even if this were to happen, though, we could just start over with a different curve and different point. This is, more-or-less, what Lenstra's algorithm boils down to: Repeatedly take multiples of $P$ until one can't add anymore, or until $kP = O$, in which case we can start over with a new curve and a new point on it!

But here's the deal: multiplying points is a computationally-expensive thing to do. Sometimes, it may be more frugal to cut our losses. We don't want to spend too much time trying to multiply a given point on a given curve. This is why many efficient implementations of Lenstra's algorithm place an upper bound on the number by which we multiply our point $P$, and get a different curve and point if a factor hasn't been found by the time we get to that multiple. For most of the numbers you will be asked to factor in this class, upper-bounds won't be much of a concern. But if you try plugging in some monstrous composite number on the order of 100 digits or so into your implementation, don't act surprised if Cocalc shuts down the Sage kernel on you!  (On the other hand, with more computational power, Lenstra's algorithm can, in fact, factor such numbers!)

### Exercise 3: Lenstra

Write a function `lenstra`, which takes a single argument `n` --- the integer we would like to find a factor of. The function will randomly choose a curve and point on said curve to start multiplying.

In [6]:
"""
All versions of the Lenstra algorithm computes successive multiples of a point P. The algorithms
differ in which successive multiples they use. In particular, on iteration i, we compute f(i)P, where
f(i) is the function giving the multiple to use on iteration i.
"""
def lenstra(P, a, n):
    """
    INPUT
     - Point 'P'
     - Coefficient 'a' which when taken with 'P' and 'n' uniquely determines the coefficient 'b' defining the elliptic curve y^2 = x^3 + ax + b
     - Modulus of congruence 'n'
    OUTPUT
     - Computed factor of 'n'

    Hint: One possible choice for f(i) is f(i) = i, that is, at step i we calculate i!*P
    """
    return # factor of n

def rand_elliptic(n):
    """
    Generates a random elliptic curve y^2 = x^3 + ax + b
    and a point P0 on that curve
    """
    P0 = randint(0, n - 1), randint(0, n - 1)
    a = randint(0, n - 1)
    return P0, a


def lenstra_random(n):
    """
    After you define the `lenstra` function above, this function will run until a proper factor is found by generating random curves
    """
    #Set g to n to guarantee entry into the loop
    g = n

    #Repeat until g is not n(i.e., a "proper factor" of n)
    while (g == n):
        P0, a = rand_elliptic(n)
        g = lenstra(P0, a, n)

    #Temporary fix to prevent error in the test cases
    return n if g is None else g
    #You will want to comment out the above line and uncomment the below line
#     return g

## Testing

In [7]:
print(elliptic_mul(189,(2,3),-10,557))
print(elliptic_mul(63,(2,3),-10,557))
print(elliptic_mul(27,(2,3),-10,557))

None
None
None


In [6]:
n = 2501
factor = lenstra_random(n)
print ("{0} is a proper factor of {1}: {1}/{0} = {2}".format(factor, n, n/factor))

2501 is a proper factor of 2501: 2501/2501 = 1


In [7]:
n = 10480711537
# for i in range(1000):
factor = lenstra_random(n)
if not factor: print("{0} failed".format(i))
print(factor)
print ("{0} is a proper factor of {1}: {1}/{0} = {2}".format(factor, n, n/factor))

10480711537
10480711537 is a proper factor of 10480711537: 10480711537/10480711537 = 1


In [8]:
n = 239931844437067
factor = lenstra_random(n)
print(factor)
print ("{0} is a proper factor of {1}: {1}/{0} = {2}".format(factor, n, n/factor))

239931844437067
239931844437067 is a proper factor of 239931844437067: 239931844437067/239931844437067 = 1


In [9]:
n = 363982776557
factor = lenstra_random(n)
print(factor)
print ("{0} is a proper factor of {1}: {1}/{0} = {2}".format(factor, n, n/factor))

363982776557
363982776557 is a proper factor of 363982776557: 363982776557/363982776557 = 1
